# Week 12 Lab 

## Maximum Likelihood Estimation of a Normal Regression Model

In assignment 11 you have studied the **normal regression model**

\begin{align*}
    Y_i &= X_i'\beta + e_i, \qquad \text{where }
    e_i | X_i \sim \mathcal{N}(0, \sigma_e^2).
\end{align*}

As you can see, the errors here are assumed to have an **exact** normal distribution. This enables us to use maximum likelihood estimation, because we know the distribution of $Y_i$ **conditional on $X_i$**.

What are we estimating? The unknown parameters are $\beta \in \R^K$ and $\sigma_e^2$.

That conditional density is
\begin{align*}
    f_{Y|X}(y | x, \beta, \sigma_e^2) = \frac{1}
        {\sqrt{ 2 \pi \sigma_e^2}} \exp \left( - \frac{1}{2 \sigma_e^2} (y - x'\beta)^2
        \right).
\end{align*}




## Loading packages for this notebook

We will be needing the following packages:

In [1]:
using LinearAlgebra, Distributions, Random, Optim

## Exercise 1

Here's a **slightly modified** version of the DGP from week 7, where we simulated Card's schooling model:

$$
\begin{align*}
    u & \sim \mathcal{N}(0, \sigma_u^2) \\
    A & \sim \mathcal{N}(0, \sigma_A^2) && \text{(ability)}\\
    S &= \pi + A && \text{(schooling)}\\
    X & \sim \text{Discrete uniform on }\{0,1,\ldots,20\}  && \text{(experience)} \\
    Y &= \exp (\beta_1 + \beta_2 S + \beta_3 X + u) && \text{(earnings)}
\end{align*}
$$

What's different from week 7?

* ability $A$ is not on the rhs of the earnings equation (which effectively removes the omitted variables bias problem)

* work experience $X$ is added on the rhs of the earnigs equation, the coefficient $\beta_3$ is the return to work experience

Why am I making these changes? I want to avoid endogeneity and I want to have more than one explanatory variable (hence the introduction of $X$.)

This model is a normal regression model when you consider the logarithm of $Y$.

Use the function `schooling_sample` (from week 7) to create a random sample of size 5,000 using these parameter values:

|                           | Calibrated values  |
|---------------------------|--------------------|
| $\beta_1$                 | 4.70               |
| $\beta_2$                 | 0.07               |
| $\beta_3$                 | 0.12               |
| $\pi$                     | 13.2               |
| $\sigma_u^2$              | 0.175              |
| $\sigma_A^2$              | 7.20               |




## Exercise 2

As you know, the log-likelihood function for this model is

$$
L = -\tfrac{N}{2} \ln \left(2 \pi \sigma_e^2 \right) 
-\frac{1}{2 \sigma_e^2} \sum (y_i - x_i' \beta)^2
$$

Use this function to obtain the MLE (for all unknown parameters).

(Make sure, along the way, to implement a closure `nll` which is the negative log-likelihood function.)

## Exercise 3

As you also know, the asymptotic result for the MLE is

\begin{align*}
    \sqrt{N}
    \begin{pmatrix}
        \hat{\beta}^\text{ML} - \beta \\
        \hat{\sigma}_e^{2,\text{ML}} - \sigma_e^2
    \end{pmatrix}
    \overset{d}{\to}
    \mathcal{N}
    \begin{pmatrix}
        \begin{pmatrix}
            0\\0
        \end{pmatrix}
        ,
        \begin{pmatrix}
            \sigma_e^2 E(X_i X_i')^{-1} &
            0 \\
            0' &
            2\sigma_e^4
        \end{pmatrix}
\end{pmatrix}.
\end{align*}

Obtain estimates of the standard errors of $\widehat{\beta}^\text{ML}$.


## Exercise 4

Instead of using the **analytical** Hessian matrix to obtain the asymptotic variance, the `Optim` package together with the `NLSolversBase` package are able to **numerically** approximate the Hessian. 

The implementation is a bit clumsy. Using your likelihood closure `nll`, you would obtain the Hessian and its diagonal like so:

In [4]:
using NLSolversBase
td = TwiceDifferentiable(nll, ones(4))
H = hessian!(td, vcat(beta, se2)) # that is the MLE for (β, σ^2)
diag(inv(H))

Are these results based on the numerical derivatives similar to the results based on the analytical derivate?